In [1]:
!pip install -q pysal contextily dask sweetviz streamlit-folium folium


In [1]:
import matplotlib.pyplot as plt
import numpy as np
import seaborn
from pysal.viz import splot
from splot.esda import plot_moran
import contextily
import os 
os.environ['USE_PYGEOS'] = '0'
import geopandas as gpd
import pandas as pd
from pysal.explore import esda
from pysal.lib import weights
from numpy.random import seed
from dask.threaded import get

import plotly.express as px


import dask
from dask.graph_manipulation import bind
import plotly.graph_objects as go
import geopandas as gpd
from plotly.subplots import make_subplots



/opt/homebrew/Caskroom/miniforge/base/envs/metaltf/lib/python3.8/site-packages/geopandas/_compat.py:123: UserWarning: The Shapely GEOS version (3.11.1-CAPI-1.17.1) is incompatible with the GEOS version PyGEOS was compiled with (3.10.4-CAPI-1.16.2). Conversions between both will be slow.
  warnings.warn(
/opt/homebrew/Caskroom/miniforge/base/envs/metaltf/lib/python3.8/site-packages/splot/_viz_esda_mpl.py:3: UserWarning: Shapely 2.0 is installed, but because PyGEOS is also installed, GeoPandas will still use PyGEOS by default for now. To force to use and test Shapely 2.0, you have to set the environment variable USE_PYGEOS=0. You can do this before starting the Python process, or in your code before importing geopandas:

import os
os.environ['USE_PYGEOS'] = '0'
import geopandas

In a future release, GeoPandas will switch to using Shapely by default. If you are using PyGEOS directly (calling PyGEOS functions on geometries from GeoPandas), this will then stop working and you are encouraged

In [2]:
# @dask.delayed
def readCrashsiteGDF()->gpd.GeoDataFrame:
    crashsite_df = pd.read_csv("../data/Road_Crashes_for_five_Years_Victoria.csv",parse_dates=["ACCIDENT_DATE"],index_col="ACCIDENT_NO")
    crashsite_gdf = gpd.GeoDataFrame(
        crashsite_df, geometry=gpd.points_from_xy(crashsite_df.LONGITUDE, crashsite_df.LATITUDE),crs="EPSG:4326"
    )

    crashsite_gdf = crashsite_gdf.to_crs(3857)
    return crashsite_gdf

# @dask.delayed
def readHexGridGDF(path="../data/grid1KM.json"):
    grid = gpd.read_file(
        path,crs=None
    )
    grid["grid_id"] = grid.index
    return grid


# @dask.delayed
def getDB(crashsite_gdf,hexgrid_gdf):
    joined = gpd.GeoDataFrame(
        hexgrid_gdf.sjoin(crashsite_gdf.to_crs(hexgrid_gdf.crs),how="left")
    )
    return joined
# @dask.delayed 
def aggregation(joined_gdf,k=6,):
    
    agged = gpd.GeoDataFrame(
    joined_gdf.groupby("grid_id").agg({
        "FATALITY":"mean",
        "geometry":"first",
        "TOTAL_PERSONS": "mean",
        "INJ_OR_FATAL": "mean",
        "FATALITY": "mean",
        "SERIOUSINJURY": "mean",
        "index_right": "count",
    })
    )
    agged.rename(columns={"index_right":"count"},inplace=True)

    data_buffer = agged.copy().dropna().query("count>0")
    w = weights.KNN.from_dataframe(data_buffer, k=k) #k is the number of neighbour
    w.transform = "R" #normalise the weights matrix

    data_buffer["count_lag"] = weights.spatial_lag.lag_spatial(
        w, data_buffer["count"]
    )
    columns = ["FATALITY","TOTAL_PERSONS","INJ_OR_FATAL","FATALITY","SERIOUSINJURY"]
    for column in columns:
        data_buffer[column+"_lag"] = weights.spatial_lag.lag_spatial(
            w, data_buffer[column]
        )

    qx = data_buffer["count"].mean()
    qy = data_buffer["count_lag"].mean()
    def get_quantile(x):

        if(x["count"]>qx and x["count_lag"]>qy):
            return "HotSpot"
        elif(x["count"]<=qx and x["count_lag"]<=qy):
            return "ColdSpot"
        elif(x["count"]>qx and x["count_lag"]<=qy):
            return "EmergingHotSpot"
        elif(x["count"]<=qx and x["count_lag"]>qy):
            return "DecliningHotSpot"
    data_buffer["count_id_quantile"] = data_buffer.apply(get_quantile,axis=1)
    return data_buffer


def make_plot(groupedHexGrid_gdf,column_name="count",title=None):
    # Assuming you have your GeoDataFrame named 'groupedHexGrid_gdf'
    # Convert GeoDataFrame to GeoJSON for Plotly
    geojson = groupedHexGrid_gdf.__geo_interface__
    # Create a Choroplethmapbox trace

    title = title if title else f"{column_name.replace('_',' ')} Rank Pct"

    choropleth_trace = go.Choroplethmapbox(
        geojson=geojson,
        locations=groupedHexGrid_gdf.index,  # Spatial coordinates
        z=(groupedHexGrid_gdf[column_name].rank(pct=True)),        
        colorscale="RdBu_r",
        colorbar={"title": title},
        marker_opacity=0.3,
        marker_line_width=2,
        marker_line_color="white",
        hovertemplate="<b>Crashsite "+column_name+"</b>: %{z}<br>" +"<b>Quantile</b>: %{z}<br>" +"<extra></extra>",
        # animation_frame=groupedHexGrid_gdf.
        
    )
    layout_choropleth = go.Layout(
        mapbox_style="carto-positron",
        mapbox_zoom=6,  # Adjust as needed
        mapbox_center={"lat": -37.8, "lon": 144.95},
        margin={"r": 0, "t": 0, "l": 0, "b": 0},

    )
    # Create the figure for the choropleth map
    fig_choropleth = go.Figure(data=[choropleth_trace], layout=layout_choropleth)
    return fig_choropleth


In [3]:
# crashsite_gdf = readCrashsiteGDF()
# hexgrid_gdf = readHexGridGDF()
# joined_gdf = getDB(crashsite_gdf,hexgrid_gdf)
# groupedHexGrid_gdf = aggregation(joined_gdf)


dsk = {'crashsite_gdf': readCrashsiteGDF,
       'hexgrid_gdf': readHexGridGDF,
       'joined_gdf': (getDB, 'crashsite_gdf', 'hexgrid_gdf'),
       'groupedHexGrid_gdf': (aggregation, 'joined_gdf'),
       "plot": (make_plot, "groupedHexGrid_gdf","INJ_OR_FATAL"),
       "lagplot": (make_plot, "groupedHexGrid_gdf", "INJ_OR_FATAL_lag")
       }


In [4]:

%%time
joined_gdf,groupedHexGrid_gdf =  get(dsk, ['joined_gdf',"groupedHexGrid_gdf"])


/opt/homebrew/Caskroom/miniforge/base/envs/metaltf/lib/python3.8/site-packages/libpysal/weights/weights.py:172: UserWarning: The weights matrix is not fully connected: 
 There are 2 disconnected components.
  warnings.warn(message)


CPU times: user 13.4 s, sys: 791 ms, total: 14.2 s
Wall time: 14.5 s


In [5]:
joined_gdf[['LONGITUDE', 'LATITUDE']].describe()

In [31]:

qx = groupedHexGrid_gdf["count"].mean()
qy = groupedHexGrid_gdf["count_lag"].mean()

In [32]:
spatialCountPlot = make_plot(groupedHexGrid_gdf,"count")
spatialCountPlot_lag = make_plot(groupedHexGrid_gdf,"count_lag")

spatialCountPlot.show()
spatialCountPlot_lag.show()